# Imports and Initialise Env

In [1]:
import mlagents
from mlagents_envs.environment import UnityEnvironment as UE
import numpy as np
from mlagents_envs.environment import ActionTuple

In [2]:
file_name1 = "C:\\Users\\Palaash.HPZ\\Desktop\\RL-concept-learning_large_build_envs\\build_envs\\windows\\S2 180723\\build"
file_name2 = "C:\\Users\\Palaash.HPZ\\Desktop\\RL-concept-learning_large_build_envs\\build_envs\\windows\\S2_test 180723\\build"

env1 =  UE(file_name=file_name1,seed=1,side_channels=[],worker_id=1,no_graphics = False)
env1.reset()

env2 =  UE(file_name=file_name2,seed=1,side_channels=[],worker_id=2,no_graphics = False)
env2.reset()

# behavior_names = list(env.behavior_specs.keys())
# behavior_value = list(env.behavior_specs.values())
# DecisionSteps, TerminalSteps = env.get_steps(behavior_names[0])
# agentsNum = len(DecisionSteps.agent_id)

In [7]:
# env1.close()
# env2.close()

#  Model

In [4]:
# model
import os
import torch
import torch.nn as nn
import torch.nn.functional as F

vision_output_dim = 3136
num_words = 35  # Number of unique words in the vocabulary
language_output_dim = 128
embedding_dim = 128
mixing_dim = 256
lstm_hidden_dim = 256
num_actions = 4

# (3,128,128) --> (64,7,7) = 3136 (3-layer CNN)
class VisualModule(nn.Module): 
    def __init__(self):
        super(VisualModule, self).__init__()
        self.conv = nn.Sequential(
            nn.Conv2d(3, 32, kernel_size=3, stride=2, padding=1),
            nn.ReLU(),
            nn.Conv2d(32, 64, kernel_size=3, stride=3, padding=1),
            nn.ReLU(),
            nn.Conv2d(64, 64, kernel_size=3, stride=3, padding=0),
            nn.ReLU()
        )
        # self.conv = nn.Sequential(
        #     nn.Conv2d(3, 32, kernel_size=5, stride=2, padding=2),
        #     nn.ReLU(),
        #     nn.Conv2d(32, 64, kernel_size=5, stride=2, padding=2),
        #     nn.ReLU(),
        #     nn.Conv2d(64, 128, kernel_size=5, stride=2, padding=2),
        #     nn.ReLU(),
        #     nn.Conv2d(128, 64, kernel_size=5, stride=2, padding=1),
        #     nn.ReLU(),
        #     nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1),
        #     nn.ReLU(),
        #     nn.Conv2d(64, 64, kernel_size=3, stride=1, padding=1),
        #     nn.ReLU(),
        # )

    def forward(self, vt):
        encoded_vt = self.conv(vt)
        return encoded_vt.view(vt.size(0), -1).squeeze()

# one-hot encoding [0 0 1 0 0] --> 128 dimensional embedding (FF)
# S1:5 S2:5 S3:11 S4:9 --> 30 + 5 (noun) = 35 in total
class LanguageModule(nn.Module): 
    def __init__(self, num_words, embedding_dim):
        super(LanguageModule, self).__init__()
        self.embedding = nn.Linear(num_words, embedding_dim)

    def forward(self, lt):
        embedded_lt = self.embedding(lt)
        return embedded_lt

# 3136(vision) + 128 (language) --> 256 dimensional embedding (FF)
class MixingModule(nn.Module):
    def __init__(self, vision_output_dim, language_output_dim, mixing_dim):
        super(MixingModule, self).__init__()
        self.linear = nn.Linear(vision_output_dim + language_output_dim, mixing_dim)

    def forward(self, vision_output, language_output):
        combined_output = torch.cat((vision_output, language_output), dim=0)
        mixed_output = self.linear(combined_output)
        return mixed_output

class LSTMModule(nn.Module):
    def __init__(self,mixing_dim,lstm_hidden_dim):
        super(LSTMModule, self).__init__()
        self.lstm = nn.LSTMCell(mixing_dim, lstm_hidden_dim)
    
    def forward(self,mixed_output,lstm_hidden_state):
        lstm_hidden_state = self.lstm(mixed_output, lstm_hidden_state) 
        # lstm_output = lstm_hidden_state[0] # output is (hidden_state,cell_state), we need hidden state, shape (1,256)
        return lstm_hidden_state

class Agent(nn.Module):
    def __init__(self, num_words, embedding_dim, vision_output_dim, language_output_dim, mixing_dim, lstm_hidden_dim,num_actions):
        super(Agent, self).__init__()
        self.language_module = LanguageModule(num_words, embedding_dim)
        self.visual_module = VisualModule()
        self.mixing_module = MixingModule(vision_output_dim, language_output_dim, mixing_dim)
        self.lstm_module = LSTMModule(mixing_dim, lstm_hidden_dim)
        self.action_predictor = nn.Linear(lstm_hidden_dim, num_actions)
        self.value_estimator = nn.Linear(lstm_hidden_dim, 1)

    def forward(self, vt, lt, lstm_hidden_state):
        vision_output = self.visual_module(vt)
        language_output = self.language_module(lt)
        mixed_output = self.mixing_module(vision_output, language_output).unsqueeze(0)
        lstm_output = self.lstm_module(mixed_output,lstm_hidden_state)
        action_probs = self.action_predictor(lstm_output[0]) 
        value_estimate = self.value_estimator(lstm_output[0])
        return action_probs,value_estimate,lstm_output
        
        
    def save(self, episode, ALG_NAME, ENV_ID):
        path = os.path.join('model', '_'.join([ALG_NAME, ENV_ID]))
        if not os.path.exists(path):
            os.makedirs(path)
        torch.save(self.state_dict(), os.path.join(path, f'agent_{episode}.pt'))

    def load(self, episode, ALG_NAME, ENV_ID):
        path = os.path.join('model', '_'.join([ALG_NAME, ENV_ID]))
        self.load_state_dict(torch.load(os.path.join(path, f'agent_{episode}.pt')))   
        
#     def load(self,path):
#         self.load_state_dict(torch.load(path))

# Train

1: with skip steps: set speed=1, lr = 3.5e-5  #LR
2: without skip steps: set speed=3, lr = 3.5e-5  #LR
3: lr = 5e-5  #LR
4: lr = 10e-5  #LR

increase LR will learn faster but training may collapse if too fast

reward structure

hit target: +10
hit wall: -1
hit wrong target: -3
max steps reached: -10

s1a 100,000 20 hrs

In [5]:
# 
import argparse
import time
import json
# import matplotlib.pyplot as plt
import os
import numpy as np
import torch
import torch.nn as nn
import torch.optim as optim
from torch.distributions import Categorical
# add arguments in command --train/test
# parser = argparse.ArgumentParser(description='Train or test neural net motor controller.')
# parser.add_argument('--train', dest='train', action='store_true', default=False)
# parser.add_argument('--test', dest='test', action='store_true', default=True)
# args = parser.parse_args()

train = True
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(device) 

# load from S0 - these are the S0 best model details
S0_ALG_NAME = 'S0'
S0_ENV_ID = '3'
S0_episode = 7593

ALG_NAME = 'S2'
ENV_ID = '8'
TRAIN_EPISODES = 200000  # number of overall episodes for training
MAX_STEPS = 500  # maximum time step in one episode
LAM = 0.95  # reward discount in TD error
env_per_iteration = 100
lr = 3.5e-5  #LR
speed = 1
num_steps = 250 # the step for updating the network
max_step_reward = -10

if __name__ == '__main__':
    agent = Agent(num_words, embedding_dim, vision_output_dim, language_output_dim, mixing_dim, lstm_hidden_dim,num_actions)
    agent.load(S0_episode,S0_ALG_NAME,S0_ENV_ID)
    agent.to(device)
    optimizer = optim.RMSprop(agent.parameters(), lr=lr)
    best_score = float('-inf') #this is -infinity
    
    object_hashmap = {
    0: 'capsule',
    1: 'cube',
    2: 'cylinder',
    3: 'prism',
    4: 'sphere'}
    colour_hashmap = {
    0: 'red',
    1: 'green',
    2: 'blue',
    3: 'yellow',
    4: 'black'}
    
    if train:
        entropy_term = 0
        all_episode_reward = []
        all_average_reward = []
        all_steps = []
        all_actor_loss = []
        all_critic_loss = []
        all_entropy_loss = []
        all_total_loss = []
        tracked_agent = -1
        
        for episode in range(TRAIN_EPISODES):
            t0 = time.time()
            episode_reward = 0
                        
            env_index = (episode // env_per_iteration) % 2
            if env_index == 0: env = env1
            else: env = env2
            behavior_name=list(env.behavior_specs)[0]
            spec=env.behavior_specs[behavior_name]
            STEPS = 0
            
            decision_steps, terminal_steps = env.get_steps(behavior_name)
            # state -- vt, lt, lstm
            vt = torch.tensor(decision_steps.obs[0]).reshape(1,3,128,128).to(device) #vector image
            object_index = int(decision_steps.obs[1][0][0])
            colour_index = int(decision_steps.obs[1][0][1])
            print(f'--- target colour: {colour_hashmap[colour_index]}, target object: {object_hashmap[object_index]} ---')
            # objects: 0-capsule,1-cube,2-cylinder,3-prism,4-sphere 
            # colours: 0-red,1-green,2-blue,3-yellow,4-black 
            
#             lt = torch.eye(num_words)[:, index].to(device) #one hot encoder language vector
            lt = torch.zeros(35).to(device)
            lt[object_index],lt[colour_index+5] = 1,1 #one hot encoder language vector
            
            lstm_hidden_state = (torch.zeros(1, lstm_hidden_dim).to(device), torch.zeros(1, lstm_hidden_dim).to(device))
            
            done = False
            while True: #training loop
                
                # Need to use when calculating the loss
                log_probs = []
                values = torch.empty(0).to(device)
                rewards = []

                for steps in range(num_steps):
                    if STEPS % 5 == 0: #this is the skip steps
                        lstm_hidden_state = tuple(tensor.detach() for tensor in lstm_hidden_state)
                        policy_dist, value, lstm_hidden_state = agent(vt,lt,lstm_hidden_state)
                    STEPS += 1
#                     lstm_hidden_state = tuple(tensor.detach() for tensor in lstm_hidden_state)
#                     policy_dist, value, lstm_hidden_state = agent(vt,lt,lstm_hidden_state)
#                     STEPS += 1
                    dist = F.softmax(policy_dist.detach(),dim=1).cpu().numpy() #use softmax to get prob dist

                    action_dist = Categorical(F.softmax(policy_dist.detach(),dim=1)) #put prob dist into Categorical class to sample
                    action = action_dist.sample() # sample an action from action_dist
                    action_onehot = F.one_hot(torch.tensor(action),num_actions).cpu()
                    
                    log_prob = torch.log(F.softmax(policy_dist,dim=1)[0][action])
                    # entropy = -np.sum(np.mean(dist)* np.log(dist))
                    entropy = F.cross_entropy(policy_dist.detach(), action)

                    discrete_actions = np.array(action_onehot).reshape(1,4)*speed
                    action_tuple = ActionTuple()
                    action_tuple.add_discrete(discrete_actions)
                    env.set_actions(behavior_name,action_tuple)
                    
                    env.step()
                    decision_steps, terminal_steps = env.get_steps(behavior_name)

                    if tracked_agent == -1 and len(decision_steps) >= 1: #means agent still req action - eps not ended yet
                        tracked_agent = decision_steps.agent_id[0]

                    if tracked_agent in terminal_steps: # roll over or hit the target
                        print('Agent in terminal steps')
                        done = True
                        reward = terminal_steps[tracked_agent].reward
                        if reward > 0:
                            pass
                        else: reward = -1 # roll over or other unseen conditions
                        print(f'Terminal Step reward: {reward}')

                    elif tracked_agent in decision_steps: # the agent which requires action
                        reward = decision_steps[tracked_agent].reward
                        if reward<0:
                            if reward==-2.5:
                                reward=-3
                                print(f'Decision Step reward: {reward}')
                            # if reward<-1: hit = 1
                            
                    if STEPS >= MAX_STEPS:
                        reward = max_step_reward
                        print(f'Max Step Reward: {reward}')
                        env.reset()
                        done = True
                    if STEPS % num_steps == 0:
                        print (f'Step: {STEPS}')

                    episode_reward = episode_reward + reward

                    rewards.append(reward)
                    # values.append(value)
                    values = torch.cat((values, value), dim=0)
                    log_probs.append(log_prob)
                    entropy_term = entropy_term + entropy
                    vt_new = torch.tensor(decision_steps.obs[0]).reshape(1,3,128,128).to(device)
                    vt = vt_new

                    if done or steps == num_steps-1:
                        break
                
                
                discounted_rewards = np.zeros_like(values.cpu().detach().numpy())
                cumulative = 0
                # print(len(rewards))
                for t in reversed(range(len(rewards))):
                    cumulative = rewards[t] + LAM * cumulative # Monte Carlo
                    discounted_rewards[t] = cumulative
                # print(f'rewards:{rewards}, discounted_rewards:{discounted_rewards}')
                # Advantage Actor Critic

                # Qvals[-1] = rewards[t] + LAM * Qval      or       Qvals[-1] = rewards[t]                   
                # for t in range(len(rewards)-1):
                #         Qvals[t] = rewards[t] + LAM * values[t+1]
                
                # r_(t+1) = R(s_t|a_t)--> reward[t]        a_t, V_t = agent(s_t)
                # A_t = r_(t+1) + LAM * V_(t+1) - V_t 
                #     = Q_t - V_t
                
                # Monte Carlo Advantage = reward + LAM * cumulative_reward
                # Actor_loss = -log(pai(s_t|a_t))*A_t
                # Critic_loss = A_t.pow(2) *0.5
                # Entropy_loss = -F.entropy(pai(St),index) * 0.001

                # entropy = -np.sum(np.mean(dist) * np.log(dist))
                
                #update actor critic
                
                # values = torch.FloatTensor(values).requires_grad_(True).to(device)
                discounted_rewards = torch.FloatTensor(discounted_rewards.astype(np.float32)).to(device)
                log_probs = torch.stack(log_probs)
                advantage = discounted_rewards - values
                actor_loss = (-log_probs * advantage).mean()
                critic_loss = 0.5 * torch.square(advantage).mean()
                entropy_term /= num_steps
                entropy_loss = -0.1 * entropy_term
                ac_loss = actor_loss + critic_loss + entropy_loss
                # ac_loss = values.mean()
                optimizer.zero_grad()
                ac_loss.backward()
                optimizer.step()
                # print('updated')
                # for name, param in agent.named_parameters():
                #     if param.grad is not None:
                #         print(name, param.grad)
                #     else:
                #         print(name, "gradients not computed")
                # for name, param in agent.named_parameters():
                #     if name == 'value_estimator.weight':
                #         print(name, param)
            
                if done: break


            all_episode_reward.append(float(episode_reward))
            all_steps.append(STEPS)
            all_actor_loss.append(float(actor_loss))
            all_critic_loss.append(float(critic_loss))
            all_entropy_loss.append(float(entropy_loss))
            all_total_loss.append(float(ac_loss))
            if episode >= 200:
                avg_score = np.mean(all_episode_reward[-200:])
                all_average_reward.append(avg_score)
                if avg_score > best_score:
                    best_score = avg_score
                    agent.save(episode, ALG_NAME, ENV_ID)
                    print(f'-----The best score for averaging previous 200 episode reward is {best_score}. Model has been saved-----')
                print('Training  | Episode: {}/{}  | Episode Reward: {:.1f}  | Average Reward {:.2f}  | Actor loss: {:.2f} | Critic loss: {:.2f} | Entropy loss: {:.4f}  | Total Loss: {:.2f} | Total Steps: {}' \
                    .format(episode + 1, TRAIN_EPISODES, episode_reward, avg_score, actor_loss, critic_loss,entropy_loss,  ac_loss, STEPS))
            else:  print('Training  | Episode: {}/{}  | Episode Reward: {:.1f}  | Actor loss: {:.2f} | Critic loss: {:.2f} | Entropy loss: {:.4f}  | Total Loss: {:.2f} | Total Steps: {}' \
                    .format(episode + 1, TRAIN_EPISODES, episode_reward, actor_loss, critic_loss, entropy_loss,  ac_loss, STEPS))
            if episode%5000 == 0:
                    agent.save(episode, ALG_NAME, ENV_ID)
                    print("Model has been saved")
        print(all_average_reward)
        agent.save(episode ,ALG_NAME, ENV_ID)
        print("Model has been saved")

        data = {
                    'all_average_reward': all_average_reward,
                    'all_episode_reward': all_episode_reward,
                    'all_actor_loss': all_actor_loss,
                    'all_critic_loss': all_critic_loss,
                    'all_entropy_loss': all_entropy_loss,
                    'all_total_loss': all_total_loss,
                    'all_steps': all_steps,
                } 
        file_path = f'result/{ALG_NAME}_{ENV_ID}.txt'
        with open(file_path, 'w') as file:
            json.dump(data, file)

cuda
--- target colour: blue, target object: prism ---


C:\Users\Palaash.HPZ\anaconda3\envs\new_mlagents\lib\site-packages\ipykernel_launcher.py:110: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 1/200000  | Episode Reward: 7.0  | Actor loss: -1.28 | Critic loss: 18.99 | Entropy loss: -0.0115  | Total Loss: 17.70 | Total Steps: 117
Model has been saved
--- target colour: red, target object: prism ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 2/200000  | Episode Reward: 1.0  | Actor loss: -1.23 | Critic loss: 27.05 | Entropy loss: -0.0116  | Total Loss: 25.81 | Total Steps: 161
--- target colour: yellow, target object: sphere ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 3/200000  | Episode Reward: -2.0  | Actor loss: -2.07 | Critic loss: 28.74 | Entropy loss: -0.0111  | Total Loss: 26.67 | Total Steps: 87
--- target colour: blue, target object: cube --

Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 28/200000  | Episode Reward: 4.0  | Actor loss: -0.38 | Critic loss: 3.36 | Entropy loss: -0.0190  | Total Loss: 2.96 | Total Steps: 99
--- target colour: blue, target object: capsule ---
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 29/200000  | Episode Reward: 7.0  | Actor loss: -0.39 | Critic loss: 3.09 | Entropy loss: -0.0199  | Total Loss: 2.68 | Total Steps: 125
--- target colour: green, target object: prism ---
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 30/200000  | Episode Reward: 4.0  | Actor loss: -0.64 | Critic loss: 5.08 | Entropy loss: -0.0352  | Total Loss: 4.41 | Total Steps: 182
--- target colour: green, target object: sphere ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step rewar

Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 55/200000  | Episode Reward: -8.0  | Actor loss: -1.36 | Critic loss: 13.52 | Entropy loss: -0.0227  | Total Loss: 12.14 | Total Steps: 135
--- target colour: green, target object: prism ---
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 56/200000  | Episode Reward: 7.0  | Actor loss: -0.35 | Critic loss: 3.42 | Entropy loss: -0.0258  | Total Loss: 3.05 | Total Steps: 147
--- target colour: green, target object: capsule ---
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 57/200000  | Episode Reward: 4.0  | Actor loss: -0.29 | Critic loss: 5.32 | Entropy loss: -0.0097  | Total Loss: 5.02 | Total Steps: 128
--- target colour: blue, target object: sphere ---
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 58/200000  | Episo

...

Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17570/200000  | Episode Reward: 10.0  | Average Reward 6.00  | Actor loss: 0.16 | Critic loss: 2.38 | Entropy loss: -0.0014  | Total Loss: 2.53 | Total Steps: 17
--- target colour: blue, target object: capsule ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17571/200000  | Episode Reward: 1.0  | Average Reward 5.95  | Actor loss: -0.27 | Critic loss: 6.07 | Entropy loss: -0.0296  | Total Loss: 5.78 | Total Steps: 184
--- target colour: yellow, target object: cylinder ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17572/200000  | Episode Reward: -2.0  | Average Reward 5.92  | Actor loss: -0.44 | Critic loss: 6.36 | Entropy loss: -0.0105  | Total Loss: 5.90 | Total Steps: 143
--- target co

Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17595/200000  | Episode Reward: -2.0  | Average Reward 5.87  | Actor loss: -0.59 | Critic loss: 3.07 | Entropy loss: -0.0258  | Total Loss: 2.46 | Total Steps: 182
--- target colour: red, target object: cylinder ---
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17596/200000  | Episode Reward: 10.0  | Average Reward 5.87  | Actor loss: 0.24 | Critic loss: 3.51 | Entropy loss: -0.0011  | Total Loss: 3.75 | Total Steps: 17
--- target colour: black, target object: cylinder ---
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17597/200000  | Episode Reward: 10.0  | Average Reward 5.92  | Actor loss: 0.17 | Critic loss: 1.29 | Entropy loss: -0.0040  | Total Loss: 1.46 | Total Steps: 90
--- target colour: blue, target object: cube ---
Decision Step reward: -3
Agent in termina

Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17621/200000  | Episode Reward: 10.0  | Average Reward 5.89  | Actor loss: 0.10 | Critic loss: 0.97 | Entropy loss: -0.0011  | Total Loss: 1.06 | Total Steps: 16
--- target colour: yellow, target object: sphere ---
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17622/200000  | Episode Reward: 10.0  | Average Reward 5.89  | Actor loss: 0.24 | Critic loss: 5.76 | Entropy loss: -0.0013  | Total Loss: 6.00 | Total Steps: 24
--- target colour: black, target object: cube ---
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17623/200000  | Episode Reward: 4.0  | Average Reward 5.86  | Actor loss: -0.26 | Critic loss: 4.97 | Entropy loss: -0.0098  | Total Loss: 4.70 | Total Steps: 139
--- target colour: red, target object: cube ---
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode:

Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17645/200000  | Episode Reward: 7.0  | Average Reward 5.58  | Actor loss: 0.00 | Critic loss: 1.99 | Entropy loss: -0.0074  | Total Loss: 1.99 | Total Steps: 157
--- target colour: yellow, target object: cube ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Step: 250
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17646/200000  | Episode Reward: -5.0  | Average Reward 5.55  | Actor loss: 0.68 | Critic loss: 4.66 | Entropy loss: -0.0030  | Total Loss: 5.33 | Total Steps: 280
--- target colour: green, target object: prism ---
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Decision Step reward: -3
Agent in terminal steps
Terminal Step reward: 10.0
Training  | Episode: 17647/200000  | Episode Reward: -2.0  | Average Reward 5.55  | Actor loss: -0.20 | Critic loss: 6

KeyboardInterrupt: 

In [6]:
# run this when you stop training prematurely
data = {
            'all_average_reward': all_average_reward,
            'all_episode_reward': all_episode_reward,
            'all_actor_loss': all_actor_loss,
            'all_critic_loss': all_critic_loss,
            'all_entropy_loss': all_entropy_loss,
            'all_total_loss': all_total_loss,
            'all_steps': all_steps,
        } 
file_path = f'result/{ALG_NAME}_{ENV_ID}.txt'
with open(file_path, 'w') as file:
    json.dump(data, file)

# Test

In [ ]:
from torch.distributions import Categorical

device = torch.device("cpu")

episode = 9190
speed = 1
MAX_STEPS = 500
TEST_EPISODES = 100
ALG_NAME = 'S0_with'
ENV_ID = '3'
tracked_agent = -1

env.reset()
agent = Agent(num_words, embedding_dim, vision_output_dim, language_output_dim, mixing_dim, lstm_hidden_dim,num_actions)
agent.load(episode,ALG_NAME,ENV_ID)
average = 0
            
for episode in range(TEST_EPISODES):
            episode_reward = 0
            # env.reset()
            behavior_name=list(env.behavior_specs)[0]
            spec=env.behavior_specs[behavior_name]
            STEPS = 0
            decision_steps, terminal_steps = env.get_steps(behavior_name)

            # state -- vt, lt, lstm        
            vt = torch.tensor(decision_steps.obs[0]).reshape(1,3,128,128).to(device) #vector image
            object_index = int(decision_steps.obs[1][0][0])
            colour_index = int(decision_steps.obs[1][0][1])
            print(f'--- target colour: {colour_hashmap[colour_index]}, target object: {object_hashmap[object_index]} ---')
            # objects: 0-capsule,1-cube,2-cylinder,3-prism,4-sphere 
            # colours: 0-red,1-green,2-blue,3-yellow,4-black 
            
#             lt = torch.eye(num_words)[:, index].to(device) #one hot encoder language vector
            lt = torch.zeros(35).to(device)
            lt[object_index],lt[colour_index+5] = 1,1 #one hot encoder language vector
        
            lstm_hidden_state = (torch.zeros(1, lstm_hidden_dim).to(device), torch.zeros(1, lstm_hidden_dim).to(device))
            done = False
            while not done:
                STEPS += 1                
                lstm_hidden_state = tuple(tensor.detach() for tensor in lstm_hidden_state)
                policy_dist, value, lstm_hidden_state = agent(vt,lt,lstm_hidden_state)
                # value = value.detach()
                dist = F.softmax(policy_dist.detach(),dim=1).cpu().numpy()
                

                action_dist = Categorical(F.softmax(policy_dist.detach(),dim=1))
                # action_dist = Categorical(F.softmax(policy_dist,dim=1))
                action = action_dist.sample() # sample an action from action_dist
                action_onehot = F.one_hot(torch.tensor(action),num_actions).cpu()

                discrete_actions = np.array(action_onehot).reshape(1,4)*speed
                action_tuple = ActionTuple()
                action_tuple.add_discrete(discrete_actions)
                env.set_actions(behavior_name,action_tuple)
                env.step()
                decision_steps, terminal_steps = env.get_steps(behavior_name)

                if tracked_agent == -1 and len(decision_steps) >= 1:
                    tracked_agent = decision_steps.agent_id[0]
                    # print(tracked_agent)

                if tracked_agent in terminal_steps: # roll over or hit the target
                    print('Agent in terminal steps')
                    done = True
                    reward = terminal_steps[tracked_agent].reward
                    if reward > 0:
                        pass
                    else: reward = -1 # roll over or other unseen conditions

                    print(f'Terminal Step reward: {reward}')

                elif tracked_agent in decision_steps: # the agent which requires action
                    reward = decision_steps[tracked_agent].reward
                    # print(f'Decision Step reward: {reward}')
                    # if reward<0:
                    #     print(f'Decision Step reward: {reward}')

                if STEPS >= MAX_STEPS:
                        reward = -10
                        print(f'Max Step Reward: {reward}')
                        env.reset()
                        done = True

                episode_reward = episode_reward + reward
                vt_new = torch.tensor(decision_steps.obs[0]).reshape(1,3,128,128).to(device)
                vt = vt_new
            average += episode_reward / TEST_EPISODES
            print(f'Episode: {episode}, Episode reward: {episode_reward}')
print(f'Average Episode Reward: {average}')


# Random Action

In [ ]:
# Try to find the optimized MAX_STEP
# speed 1: 10000+ speed 2:1822 speed 3: 1918 speed 4: 900 speed 5: 951 speed 6:964 speed 7: 1181 
import random
import torch
import torch.nn.functional as F
# speed = 1
TRAIN_EPISODES = 20
tracked_agent = -1
num_actions = 4
average = 0
# for speed in range(30,70,5):
#     speed = speed/10
speed = 3
for episode in range(TRAIN_EPISODES):
    env.reset()
    behavior_name=list(env.behavior_specs)[0]
    step = 0
    while True:
        index = random.randint(0, 3) # sample an action from action_dist
        action_onehot = F.one_hot(torch.tensor(index),num_actions).cpu()
        discrete_actions = np.array(action_onehot).reshape(1,4)*speed #[forward, backward, right, left]
        action_tuple = ActionTuple()
        action_tuple.add_discrete(discrete_actions)
        env.set_actions(behavior_name,action_tuple)
        env.step()
        step += 1

        decision_steps, terminal_steps = env.get_steps(behavior_name)
        if tracked_agent == -1 and len(decision_steps) >= 1:
            tracked_agent = decision_steps.agent_id[0]
            
        if tracked_agent in terminal_steps: # roll over or hit the target
            reward = terminal_steps[tracked_agent].reward
            if reward > 0: # hit the target
                print(f'{episode}: {step} in total')
                average += step
                break
            else:           # roll over or other conditions
                env.reset()
                step = 0
                continue # roll over or other unseen conditions
        if tracked_agent in decision_steps: # the agent which requires action
            continue
average /= TRAIN_EPISODES
print(f'For speed {speed}, average random step for hitting the target is {average}')
      

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

# Sample data
object_sizes = [1, 2, 3, 4, 5]  # Object sizes on the x-axis
max_steps = [[4721, 2468, 1587, 1249, 1084],   # Max steps for each object size
             [4027, 1550, 738, 640, 505],
             [3320, 1391, 464, 331, 307],
             [3289, 882, 679, 424, 211],
             [3057, 1203, 470, 378, 222]]
speeds = [1, 2, 3, 4, 5]  # Discrete speeds for color-coding

# Color mapping for each speed
speed_color_mapping = {
    1: 'red',
    2: 'blue',
    3: 'green',
    4: 'orange',
    5: 'purple'
}

# Generate scatter plot
for i, size in enumerate(object_sizes):
    for j, steps in enumerate(max_steps[i]):
        speed = speeds[j]
        color = speed_color_mapping[speed]
        plt.scatter(size, steps, c=color)

# Set labels and title
plt.xlabel('Object Size')
plt.ylabel('Max Step')
plt.title('Scatter Plot')

plt.xlim(0, 6)
plt.xticks(np.arange(0, 7, 1))
plt.ylim(0, 5000)
plt.yticks(np.arange(0, 5001, 200))

# Create legend
legend_labels = [f'Speed {speed}' for speed, _ in speed_color_mapping.items()]
plt.legend(legend_labels, loc='upper right')

# Display the plot
plt.show()


